In [1]:
import pandas as pd
import os
import numpy as np
import tensorflow as tf
from tensorflow import keras
from keras import layers, Model

from sklearn.utils.class_weight import compute_class_weight

from matplotlib import pyplot as plt

from datetime import datetime

import pickle

from PIL import Image

from custom_class import *

print(f"pd.__version__: {pd.__version__}")
print(f"tf.__version__: {tf.__version__}")

image_shape = (120, 160, 3)

2025-03-26 14:38:35.739707: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-03-26 14:38:35.779315: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-03-26 14:38:35.779348: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-03-26 14:38:35.780520: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-03-26 14:38:35.787905: I tensorflow/core/platform/cpu_feature_guar

pd.__version__: 2.2.3
tf.__version__: 2.15.1


In [2]:
speed_heads = []
arrow_heads = []
arrow_turn_heads = []
angle_heads = []

In [3]:
angle_weight_paths = [
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250319_2218_try/angle_model_20250319_2218.weights.h5",
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250319_2229_try/angle_model_20250319_2229.weights.h5",
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250319_2345_try/angle_model_20250319_2345.weights.h5",
]

arrow_weight_paths = [
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250320_0023_arrow_1/angle_model_20250320_0023.weights.h5",
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250321_1538_arrow/angle_model_20250321_1538.weights.h5",
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250321_1615_arrow/angle_model_20250321_1615.weights.h5",
]

arrow_turn_weight_paths = [
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250320_1119_arrow_turn_1/angle_model_20250320_1119.weights.h5",
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250320_1139_arrow_turn_2/angle_model_20250320_1139.weights.h5",
    "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/angle_model_20250320_1200_arrow_turn_3/angle_model_20250320_1200.weights.h5",
]

# speed_weight_paths = [
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250319_1837_try/speed_model_20250319_1837.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250319_2003_try/speed_model_20250319_2003.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250319_2022_try/speed_model_20250319_2022.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250319_2042_try/speed_model_20250319_2042.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250319_2129_try/speed_model_20250319_2129.weights.h5",
# ]

# speed_weight_paths = [
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250319_1837_try/speed_model_20250319_1837.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250319_2003_try/speed_model_20250319_2003.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250321_1423_try/speed_model_20250321_1423.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250321_1355_try/speed_model_20250321_1355.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250321_1323_try/speed_model_20250321_1323.weights.h5",
# ]

# speed_weight_paths = [
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250324_1442_try2/speed_model_20250324_1442.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250324_1503_try2/speed_model_20250324_1503.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250324_1514_try2/speed_model_20250324_1514.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250324_1543_try2/speed_model_20250324_1543.weights.h5",
#     "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250324_1557_try2/speed_model_20250324_1557.weights.h5"
# ]

speed_weight_paths = [
  "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250326_1410_try3/speed_model_20250326_1410.weights.h5",
  "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250326_1421_try3/speed_model_20250326_1421.weights.h5",
  "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Models/speed_model_20250326_1433_try3/speed_model_20250326_1433.weights.h5"
]

In [4]:
# needed_heads_angle = [
#     [5, 6, 7],
#     [0, 1],
# ]

# needed_heads_speed = [
#     [1, 6, 8],
#     [1, 3],
# ]

total_num_of_heads = len(angle_weight_paths) + len(speed_weight_paths) + len(arrow_weight_paths) + len(arrow_turn_weight_paths)

In [5]:
mobilenetv3 = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)

backbone = Model(inputs=mobilenetv3.input, outputs=mobilenetv3.layers[-6].output, name="MobileNetV3Small_backbone")
neck = Model(inputs=mobilenetv3.layers[-6].output, outputs=mobilenetv3.output, name="MobileNetV3Small_neck")
neck_out = neck(backbone.output)

2025-03-26 14:38:37.980820: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2025-03-26 14:38:38.020150: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2025-03-26 14:38:38.020195: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2025-03-26 14:38:38.025236: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:887] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2025-03-26 14:38:38.025298: I external/local_xla/xla/stream_executor

### Angle

#### Angle model 0

In [6]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 0
i = 0

a = feature_extractor
a = layers.Conv2D(64, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(48, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(48, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout')(a)

# Branch 1: Angle (regression, 0 to 1)
angle_output = layers.Dense(1, activation='sigmoid', name='angle')(a)

a_model.append(a)


angle_model = Model(inputs=base_model.input, outputs={
  "angle": angle_output,
}, name="angle_model")


angle_model.load_weights(angle_weight_paths[len(angle_heads)])

# model.summary()

(None, 4, 5, 576)


In [7]:
# needed = []
# for i in needed_heads_angle[len(angle_heads)]:
#     needed.append(angle_model.outputs[i])

angle_heads.append(Model(inputs=base_model.layers[-6].output, outputs=angle_model.output, name=f"angle_head_{len(angle_heads)}"))

#### Angle model 1

In [8]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 1
i = 0

a = feature_extractor
a = layers.Conv2D(64, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(52, (3, 3), (2, 2), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(36, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout')(a)

# Branch 1: Angle (regression, 0 to 1)
angle_output = layers.Dense(1, activation='sigmoid', name='angle')(a)


angle_model = Model(inputs=base_model.input, outputs={
  "angle": angle_output,
}, name="angle_model")


angle_model.load_weights(angle_weight_paths[len(angle_heads)])

# model.summary()

(None, 4, 5, 576)


In [9]:
angle_heads.append(Model(inputs=base_model.layers[-6].output, outputs=angle_model.output, name=f"angle_head_{len(angle_heads)}"))

#### Angle model 2

In [10]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 2
i = 0

a = feature_extractor
a = layers.Conv2D(96, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(64, (3, 3), (2, 2), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(96, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(56, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout')(a)

# Branch 1: Angle (regression, 0 to 1)
angle_output = layers.Dense(1, activation='sigmoid', name='angle')(a)


angle_model = Model(inputs=base_model.input, outputs={
  "angle": angle_output,
}, name="angle_model")


angle_model.load_weights(angle_weight_paths[len(angle_heads)])

# model.summary()

(None, 4, 5, 576)


In [11]:
angle_heads.append(Model(inputs=base_model.layers[-6].output, outputs=angle_model.output, name=f"angle_head_{len(angle_heads)}"))

#### Merge angle heads

In [12]:
angle_heads_out = [angle_head(backbone.output) for angle_head in angle_heads]
angle_heads_out

[{'angle': <KerasTensor: shape=(None, 1) dtype=float32 (created by layer 'angle_head_0')>},
 {'angle': <KerasTensor: shape=(None, 1) dtype=float32 (created by layer 'angle_head_1')>},
 {'angle': <KerasTensor: shape=(None, 1) dtype=float32 (created by layer 'angle_head_2')>}]

In [13]:
# angle_head = Model(inputs=base_model.get_layer("expanded_conv_14/Add").output, outputs=angle_model.output, name="angle_head")

### Arrow

#### Arrow model 0

In [14]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 0
i = 0

a = feature_extractor
a = layers.Conv2D(128, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(86, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(128, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.3, name=f'a{i}_dropout')(a)

# Branch 1: No arrow (regression, 0 to 1)
arrow_output = layers.Dense(3, activation="softmax", name='no_arrow_output')(a)


arrow_model = Model(inputs=base_model.input, outputs={
  "arrow": arrow_output,
}, name="arrow_model")


arrow_model.load_weights(arrow_weight_paths[len(arrow_heads)])

# model.summary()

(None, 4, 5, 576)


In [15]:
arrow_heads.append(Model(inputs=base_model.layers[-6].output, outputs=arrow_model.output, name=f"arrow_head_{len(arrow_heads)}"))

#### Arrow model 1

In [16]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 1
i = 0

a = feature_extractor
a = layers.Conv2D(196, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(128, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(128, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.3, name=f'a{i}_dropout')(a)

# Branch 1: No arrow (regression, 0 to 1)
arrow_output = layers.Dense(3, activation="softmax", name='no_arrow_output')(a)


arrow_model = Model(inputs=base_model.input, outputs={
  "arrow": arrow_output,
}, name="arrow_model")


arrow_model.load_weights(arrow_weight_paths[len(arrow_heads)])

# model.summary()

(None, 4, 5, 576)


In [17]:
arrow_heads.append(Model(inputs=base_model.layers[-6].output, outputs=arrow_model.output, name=f"arrow_head_{len(arrow_heads)}"))

#### Arrow model 2

In [18]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 2
i = 0

a = feature_extractor
a = layers.Conv2D(384, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(128, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(96, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout')(a)

# Branch 1: No arrow (regression, 0 to 1)
arrow_output = layers.Dense(3, activation="softmax", name='no_arrow_output')(a)


arrow_model = Model(inputs=base_model.input, outputs={
  "arrow": arrow_output,
}, name="arrow_model")


arrow_model.load_weights(arrow_weight_paths[len(arrow_heads)])

# model.summary()

(None, 4, 5, 576)


In [19]:
arrow_heads.append(Model(inputs=base_model.layers[-6].output, outputs=arrow_model.output, name=f"arrow_head_{len(arrow_heads)}"))

#### Merge arrow heads

In [20]:
arrow_heads_out = [arrow_head(backbone.output) for arrow_head in arrow_heads]
arrow_heads_out

[{'arrow': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'arrow_head_0')>},
 {'arrow': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'arrow_head_1')>},
 {'arrow': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'arrow_head_2')>}]

### Arrow Turn

#### Arrow_turn model 0

In [21]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 0
i = 0

a = feature_extractor
a = layers.Conv2D(128, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(64, (3, 3), (2, 2), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(96, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout')(a)

# Branch 1: No arrow (regression, 0 to 1)
arrow_output = layers.Dense(3, activation="softmax", name='no_arrow_output')(a)


arrow_turn_model = Model(inputs=base_model.input, outputs={
  "arrow_turn": arrow_output,
}, name="arrow_turn_model")


arrow_turn_model.load_weights(arrow_turn_weight_paths[len(arrow_turn_heads)])

# model.summary()

(None, 4, 5, 576)


In [22]:
arrow_turn_heads.append(Model(inputs=base_model.layers[-6].output, outputs=arrow_turn_model.output, name=f"arrow_turn_head_{len(arrow_turn_heads)}"))

#### Arrow_turn model 1

In [23]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 1
i = 0

a = feature_extractor
a = layers.Conv2D(96, (3, 3), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_2')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_2')(a)
a = layers.Activation('relu', name=f'a{i}_relu_2')(a)
a = layers.Conv2D(64, (3, 3), (2, 2), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(36, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout')(a)

# Branch 1: No arrow (regression, 0 to 1)
arrow_output = layers.Dense(3, activation="softmax", name='no_arrow_output')(a)


arrow_turn_model = Model(inputs=base_model.input, outputs={
  "arrow_turn": arrow_output,
}, name="arrow_turn_model")


arrow_turn_model.load_weights(arrow_turn_weight_paths[len(arrow_turn_heads)])

# model.summary()

(None, 4, 5, 576)


In [24]:
arrow_turn_heads.append(Model(inputs=base_model.layers[-6].output, outputs=arrow_turn_model.output, name=f"arrow_turn_head_{len(arrow_turn_heads)}"))

#### Arrow_turn model 2

In [25]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False, 
)
base_model.trainable = False

feature_extractor = base_model.output

print(feature_extractor.shape)

a_model = []

output_activation_1 = 'sigmoid'


# model 2
i = 0

a = feature_extractor

a = layers.Conv2D(64, (3, 3), (2, 2), padding='same', 
                  kernel_initializer='he_uniform', name=f'a{i}_conv_1')(feature_extractor)
a = layers.BatchNormalization(name=f'a{i}_bn_1')(a)
a = layers.Activation('relu', name=f'a{i}_relu_1')(a)
a = layers.GlobalAveragePooling2D(name=f'a{i}_GAP')(a)
a = layers.Dense(64, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_2')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout_2')(a)
a = layers.Dense(48, activation='relu', kernel_initializer='he_uniform', name=f'a{i}_dense_1')(a)
a = layers.Dropout(0.5, name=f'a{i}_dropout')(a)

# Branch 1: No arrow (regression, 0 to 1)
arrow_output = layers.Dense(3, activation="softmax", name='no_arrow_output')(a)


arrow_turn_model = Model(inputs=base_model.input, outputs={
  "arrow_turn": arrow_output,
}, name="arrow_turn_model")


arrow_turn_model.load_weights(arrow_turn_weight_paths[len(arrow_turn_heads)])

# model.summary()

(None, 4, 5, 576)


In [26]:
arrow_turn_heads.append(Model(inputs=base_model.layers[-6].output, outputs=arrow_turn_model.output, name=f"arrow_turn_head_{len(arrow_turn_heads)}"))

#### Merge arrow_turn heads

In [27]:
arrow_turn_heads_out = [arrow_turn_head(backbone.output) for arrow_turn_head in arrow_turn_heads]
arrow_turn_heads_out

[{'arrow_turn': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'arrow_turn_head_0')>},
 {'arrow_turn': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'arrow_turn_head_1')>},
 {'arrow_turn': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'arrow_turn_head_2')>}]

### Speed

#### Speed model 0

In [28]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False,
)

feature_extractor = base_model.output

print(feature_extractor.shape)

s_model = []


# model 0
i = 0

s = feature_extractor

s = layers.Conv2D(36,(3, 3),(2, 2),padding="same",
                  kernel_initializer="he_uniform",name=f"s{i}_conv_1",)(feature_extractor)
s = layers.BatchNormalization(name=f"s{i}_bn_1")(s)
s = layers.Activation("relu", name=f"s{i}_relu_1")(s)
s = layers.GlobalAveragePooling2D(name=f"s{i}_GAP")(s)
# s = layers.Flatten(name=f"s{i}_flatten")(s)

s = layers.Dense(48, activation="relu", kernel_initializer="he_uniform", name=f"s{i}_dense_1")(s)
s = layers.Dropout(0.5, name=f"s{i}_dropout")(s)
s = layers.Dense(3, activation="softmax", name=f"s{i}_output")(s)

s_model.append(s)


outputs_dict = {}

for i in range(len(s_model)):
    outputs_dict[f"speed{i}_output"] = s_model[i]


speed_model = Model(inputs=base_model.input, outputs=outputs_dict, name="speed_model")

speed_model.load_weights(speed_weight_paths[len(speed_heads)])
# model.summary()

(None, 4, 5, 576)


In [29]:
# needed = []
# for i in needed_heads_speed[len(speed_heads)]:
#   needed.append(speed_model.outputs[i])

speed_heads.append(Model(inputs=base_model.layers[-6].output, outputs=speed_model.output, name=f"speed_head_{len(speed_heads)}"))
# speed_heads.append(Model(inputs=base_model.output, outputs=needed, name=f"speed_head_{len(speed_heads)}"))
# speed_head = Model(inputs=base_model.output, outputs=speed_model.output, name="speed_head")

#### Speed model 1

In [30]:
base_model = keras.applications.MobileNetV3Small(
    include_top=False,
    weights="imagenet",
    input_shape=image_shape,
    pooling=None,
    include_preprocessing=False,
)

feature_extractor = base_model.output

print(feature_extractor.shape)

s_model = []


# model 1
i = 0

s = feature_extractor

s = layers.Conv2D(36,(3, 3),(2, 2),padding="same",
                  kernel_initializer="he_uniform",name=f"s{i}_conv_1",)(feature_extractor)
s = layers.BatchNormalization(name=f"s{i}_bn_1")(s)
s = layers.Activation("relu", name=f"s{i}_relu_1")(s)
s = layers.GlobalAveragePooling2D(name=f"s{i}_GAP")(s)
# s = layers.Flatten(name=f"s{i}_flatten")(s)

s = layers.Dense(48, activation="relu", kernel_initializer="he_uniform", name=f"s{i}_dense_1")(s)
s = layers.Dropout(0.5, name=f"s{i}_dropout")(s)
s = layers.Dense(3, activation="softmax", name=f"s{i}_output")(s)

s_model.append(s)


outputs_dict = {}

for i in range(len(s_model)):
    outputs_dict[f"speed{i}_output"] = s_model[i]


speed_model = Model(inputs=base_model.input, outputs=outputs_dict, name="speed_model")

speed_model.load_weights(speed_weight_paths[len(speed_heads)])
# model.summary()

(None, 4, 5, 576)


In [31]:
speed_heads.append(Model(inputs=base_model.layers[-6].output, outputs=speed_model.output, name=f"speed_head_{len(speed_heads)}"))

#### Speed model 2

In [32]:
# base_model = keras.applications.MobileNetV3Small(
#     include_top=False,
#     weights="imagenet",
#     input_shape=image_shape,
#     pooling=None,
#     include_preprocessing=False,
# )

# feature_extractor = base_model.output

# print(feature_extractor.shape)

# s_model = []


# # model 2
# i = 0

# s = feature_extractor

# s = layers.Conv2D(30,(3, 3),(2, 2),padding="same",
#                   kernel_initializer="he_uniform",name=f"s{i}_conv_1",)(feature_extractor)
# s = layers.BatchNormalization(name=f"s{i}_bn_1")(s)
# s = layers.Activation("relu", name=f"s{i}_relu_1")(s)
# s = layers.GlobalAveragePooling2D(name=f"s{i}_GAP")(s)
# # s = layers.Flatten(name=f"s{i}_flatten")(s)

# s = layers.Dense(36, activation="relu", kernel_initializer="he_uniform", name=f"s{i}_dense_1")(s)
# s = layers.Dropout(0.5, name=f"s{i}_dropout")(s)
# s = layers.Dense(3, activation="softmax", name=f"s{i}_output")(s)

# s_model.append(s)



# outputs_dict = {}

# for i in range(len(s_model)):
#     outputs_dict[f"speed{i}_output"] = s_model[i]


# speed_model = Model(inputs=base_model.input, outputs=outputs_dict, name="speed_model")

# speed_model.load_weights(speed_weight_paths[len(speed_heads)])
# # model.summary()

In [33]:
speed_heads.append(Model(inputs=base_model.layers[-6].output, outputs=speed_model.output, name=f"speed_head_{len(speed_heads)}"))

#### Speed model 3

In [34]:
# base_model = keras.applications.MobileNetV3Small(
#     include_top=False,
#     weights="imagenet",
#     input_shape=image_shape,
#     pooling=None,
#     include_preprocessing=False,
# )

# feature_extractor = base_model.output

# print(feature_extractor.shape)

# s_model = []


# # model 3
# i = 0

# s = feature_extractor

# s = layers.Conv2D(64,(3, 3),(2, 2),padding="same",
#                   kernel_initializer="he_uniform",name=f"s{i}_conv_1",)(feature_extractor)
# s = layers.BatchNormalization(name=f"s{i}_bn_1")(s)
# s = layers.Activation("relu", name=f"s{i}_relu_1")(s)
# s = layers.GlobalAveragePooling2D(name=f"s{i}_GAP")(s)
# # s = layers.Flatten(name=f"s{i}_flatten")(s)

# s = layers.Dense(86, activation="relu", kernel_initializer="he_uniform", name=f"s{i}_dense_2")(s)
# s = layers.Dropout(0.5, name=f"s{i}_dropout_2")(s)
# s = layers.Dense(48, activation="relu", kernel_initializer="he_uniform", name=f"s{i}_dense_1")(s)
# s = layers.Dropout(0.5, name=f"s{i}_dropout")(s)
# s = layers.Dense(3, activation="softmax", name=f"s{i}_output")(s)

# s_model.append(s)



# outputs_dict = {}

# for i in range(len(s_model)):
#     outputs_dict[f"speed{i}_output"] = s_model[i]


# speed_model = Model(inputs=base_model.input, outputs=outputs_dict, name="speed_model")

# speed_model.load_weights(speed_weight_paths[len(speed_heads)])
# # model.summary()

In [35]:
# speed_heads.append(Model(inputs=base_model.layers[-6].output, outputs=speed_model.output, name=f"speed_head_{len(speed_heads)}"))

#### Speed model 4

In [36]:
# base_model = keras.applications.MobileNetV3Small(
#     include_top=False,
#     weights="imagenet",
#     input_shape=image_shape,
#     pooling=None,
#     include_preprocessing=False,
# )

# feature_extractor = base_model.output

# print(feature_extractor.shape)

# s_model = []


# # model 4
# i = 0

# s = feature_extractor

# s = layers.Conv2D(64,(3, 3),(2, 2),padding="same",
#                   kernel_initializer="he_uniform",name=f"s{i}_conv_1",)(feature_extractor)
# s = layers.BatchNormalization(name=f"s{i}_bn_1")(s)
# s = layers.Activation("relu", name=f"s{i}_relu_1")(s)
# s = layers.GlobalAveragePooling2D(name=f"s{i}_GAP")(s)
# # s = layers.Flatten(name=f"s{i}_flatten")(s)

# s = layers.Dense(128, activation="relu", kernel_initializer="he_uniform", name=f"s{i}_dense_2")(s)
# s = layers.Dropout(0.5, name=f"s{i}_dropout_2")(s)
# s = layers.Dense(52, activation="relu", kernel_initializer="he_uniform", name=f"s{i}_dense_1")(s)
# s = layers.Dropout(0.5, name=f"s{i}_dropout")(s)
# s = layers.Dense(3, activation="softmax", name=f"s{i}_output")(s)

# s_model.append(s)



# outputs_dict = {}

# for i in range(len(s_model)):
#     outputs_dict[f"speed{i}_output"] = s_model[i]


# speed_model = Model(inputs=base_model.input, outputs=outputs_dict, name="speed_model")

# speed_model.load_weights(speed_weight_paths[len(speed_heads)])
# # model.summary()

In [37]:
# speed_heads.append(Model(inputs=base_model.layers[-6].output, outputs=speed_model.output, name=f"speed_head_{len(speed_heads)}"))

#### Merge speed heads

In [38]:
speed_heads_out = [speed_head(backbone.output) for speed_head in speed_heads]
speed_heads_out

[{'speed0_output': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'speed_head_0')>},
 {'speed0_output': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'speed_head_1')>},
 {'speed0_output': <KerasTensor: shape=(None, 3) dtype=float32 (created by layer 'speed_head_2')>}]

In [39]:
# merged_model = Model(inputs=backbone.input, outputs=speed_heads_out, name="merged_model")

### Merge model

In [40]:
merged_model = Model(inputs=backbone.input, outputs=angle_heads_out + arrow_heads_out + arrow_turn_heads_out + speed_heads_out, name="merged_model")
# merged_model = Model(inputs=backbone.input, outputs=[angle_head(backbone.output)] + speed_heads_out, name="merged_model")

In [41]:
tf.keras.utils.plot_model(
    merged_model,
    show_shapes=True,  # Show input/output shapes
    show_layer_names=True,  # Show layer names (e.g., "angle_hidden_2")
    expand_nested=False,  # Keep it flat (no base_model nesting)
    show_layer_activations=True,
    dpi=96,  # Image resolution
)

In [42]:
dataset_dir = "Dataset/machine-learning-in-science-ii-2025/test_data/test_data"

ds = tf.data.Dataset.list_files(
    os.path.join(dataset_dir, "*"), shuffle=False
)
image_count = len(ds)

for f in ds.take(5):
    print(f.numpy())

# Extract image IDs
def extract_image_id(file_path):
    file_path = file_path.numpy().decode("utf-8")  # Convert from bytes to string
    filename = os.path.basename(file_path)  # Extract "1.png", "10.png", etc.
    image_id = filename.split(".")[0]  # Extract "1", "10", "100"
    return image_id

image_id_list = []

for path in ds:
    image_id_list.append(extract_image_id(path))

image_id_list = np.array(image_id_list)

def decode_img(img):
    # Convert the compressed string to a 3D uint8 tensor
    img = tf.io.decode_png(img, channels=3)
    img = tf.image.convert_image_dtype(img, tf.float32)
    return img

def process_path(file_path):
    # Load the raw data from the file as a string
    img = tf.io.read_file(file_path)
    img = decode_img(img)
    return img

ds = ds.map(process_path, num_parallel_calls=tf.data.AUTOTUNE)

def scale_ds(image):
    # Range of input image: [0, 1]
    return image * 2 - 1.0

ds = ds.map(scale_ds, num_parallel_calls=tf.data.AUTOTUNE)

def resize_ds(image):
    return tf.image.resize(image, [image_shape[0], image_shape[1]])

ds = ds.map(resize_ds, num_parallel_calls=tf.data.AUTOTUNE)

def configure_for_performance(ds):
    ds = ds.batch(1, drop_remainder=False)
    ds = ds.prefetch(buffer_size=tf.data.AUTOTUNE)
    return ds

ds = configure_for_performance(ds)

b'Dataset/machine-learning-in-science-ii-2025/test_data/test_data/1.png'
b'Dataset/machine-learning-in-science-ii-2025/test_data/test_data/10.png'
b'Dataset/machine-learning-in-science-ii-2025/test_data/test_data/100.png'
b'Dataset/machine-learning-in-science-ii-2025/test_data/test_data/1000.png'
b'Dataset/machine-learning-in-science-ii-2025/test_data/test_data/1001.png'


In [43]:
preds = merged_model.predict(ds)

2025-03-26 14:39:10.736868: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:454] Loaded cuDNN version 8904
2025-03-26 14:39:10.890192: I external/local_tsl/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2025-03-26 14:39:11.450611: I external/local_tsl/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory


1020/1020 [==============================] - 19s 16ms/step


In [44]:
# preds[1]["speed0_output"][:, 0]

In [45]:
# angle_preds = preds[0:2]
# angle_preds_list = []

# for angle_pred in angle_preds:
#     for ap in angle_pred:
#         angle_preds_list.append(ap[:, 0])

# angle_preds_list = np.array(angle_preds_list)

# angle_preds_list = np.where(np.abs(angle_preds_list - 0.5) < 0.1, angle_preds_list, (angle_preds_list - 0.5) * 1.1 + 0.5)

# angle_pred = np.mean(angle_preds_list, axis=0)
 
# print(angle_pred)

# angle_pred_df = pd.DataFrame({"image_id": image_id_list.astype(int), "angle": angle_pred}).set_index('image_id')
# # angle_pred_df.sort_index().to_csv("test_angle_pred.csv")

In [46]:
# speed_preds = preds[2:]
# speed_preds_list = []

# for speed_pred in speed_preds:
#     for sp in speed_pred:
#         speed_preds_list.append(sp[:, 0])


# # speed_preds_list = []
# # for speed_pred in speed_preds:
# #     speed_preds_list.append(speed_pred[0][:, 0])
# #     speed_preds_list.append(speed_pred[1][:, 0])

# # speed_preds = np.mean(speed_preds_list, axis=0)
# # speed_preds[0][0]

# speed_preds_list = np.array(speed_preds_list)

# speed_preds_list.mean(axis=0)

### Convert model into TFLite

In [47]:
converter = tf.lite.TFLiteConverter.from_keras_model(merged_model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]  # Enable optimization
tflite_model = converter.convert()

tf_lite_file_name = f"merged_model_{image_shape[0]}x{image_shape[1]}_{total_num_of_heads}heads.tflite"

with open(tf_lite_file_name, "wb") as f:
    f.write(tflite_model)

print(f"TFLite model: merged_model_{image_shape[0]}x{image_shape[1]}.tflite saved successfully!")

INFO:tensorflow:Assets written to: /tmp/tmppar99i1_/assets


INFO:tensorflow:Assets written to: /tmp/tmppar99i1_/assets
2025-03-26 14:39:52.407470: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:378] Ignored output_format.
2025-03-26 14:39:52.407525: W tensorflow/compiler/mlir/lite/python/tf_tfl_flatbuffer_helpers.cc:381] Ignored drop_control_dependency.
2025-03-26 14:39:52.408244: I tensorflow/cc/saved_model/reader.cc:83] Reading SavedModel from: /tmp/tmppar99i1_
2025-03-26 14:39:52.440488: I tensorflow/cc/saved_model/reader.cc:51] Reading meta graph with tags { serve }
2025-03-26 14:39:52.440521: I tensorflow/cc/saved_model/reader.cc:146] Reading SavedModel debug info (if present) from: /tmp/tmppar99i1_
2025-03-26 14:39:52.508452: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:388] MLIR V1 optimization pass is not enabled
2025-03-26 14:39:52.542086: I tensorflow/cc/saved_model/loader.cc:233] Restoring SavedModel bundle.
2025-03-26 14:39:53.054552: I tensorflow/cc/saved_model/loader.cc:217] Running initializatio

TFLite model: merged_model_120x160.tflite saved successfully!


In [48]:
import numpy as np
import tensorflow.lite as tflite  # Use this if full TensorFlow is installed
# If using tflite-runtime, import this instead:
# import tflite_runtime.interpreter as tflite

# Load TFLite model
interpreter = tflite.Interpreter(model_path=tf_lite_file_name)
interpreter.allocate_tensors()

# Get input and output details
input_details = interpreter.get_input_details()
output_details = interpreter.get_output_details()

# Create a dummy input (modify based on model input shape)
input_data = "/mnt/c/Users/psamt/OneDrive - The University of Nottingham/_Spring/PHYS4036_Machine Learning in Science Part II/Project/Dataset/machine-learning-in-science-ii-2025/test_data/test_data/1.png"
input_data = np.array(Image.open(input_data).convert('RGB').resize((image_shape[1], image_shape[0])))

# convert to range(-1, 1)
input_data = input_data / 255 * 2 - 1

input_data = input_data.astype(np.float32)

input_data = np.expand_dims(input_data, axis=0)

# Set input tensor
interpreter.set_tensor(input_details[0]['index'], input_data)

# Run inference
interpreter.invoke()

INFO: Created TensorFlow Lite XNNPACK delegate for CPU.


In [49]:
# output_details = interpreter.get_output_details()
# output_dict = {o['name']: o['index'] for o in output_details}

# angle_outputs = [interpreter.get_tensor(output_dict[f'StatefulPartitionedCall:{i}']) for i in range(10)]
# speed_outputs = [interpreter.get_tensor(output_dict[f'StatefulPartitionedCall:{i}']) for i in range(10, 20)]

In [50]:
output_details_sorted = sorted(output_details, key=lambda x: int(x['name'].split(':')[-1]))

all_outputs = [interpreter.get_tensor(out['index']) for out in output_details_sorted]

all_outputs

[array([[0.6781636]], dtype=float32),
 array([[0.7785422]], dtype=float32),
 array([[0.7420213]], dtype=float32),
 array([[1.000000e+00, 9.250487e-11, 5.938492e-09]], dtype=float32),
 array([[9.9999857e-01, 1.1219408e-10, 1.3848918e-06]], dtype=float32),
 array([[9.9999821e-01, 4.4721414e-12, 1.7708905e-06]], dtype=float32),
 array([[1.0000000e+00, 1.1089500e-09, 3.1407732e-10]], dtype=float32),
 array([[1.0000000e+00, 2.4582116e-13, 9.2330128e-16]], dtype=float32),
 array([[1.0000000e+00, 9.2736561e-13, 3.6866936e-14]], dtype=float32),
 array([[1.158079e-08, 1.441911e-10, 1.000000e+00]], dtype=float32),
 array([[8.3566425e-07, 1.0185183e-09, 9.9999917e-01]], dtype=float32),
 array([[8.3566425e-07, 1.0185183e-09, 9.9999917e-01]], dtype=float32)]

In [51]:
arrow_left = int(np.mean(np.squeeze(all_outputs[len(angle_heads):len(angle_heads)+len(arrow_heads)])[:, 1]) > 0.5)
arrow_right = int(np.mean(np.squeeze(all_outputs[len(angle_heads):len(angle_heads)+len(arrow_heads)])[:, 2]) > 0.5)

In [52]:
arrow_turn_left = int(np.mean(np.squeeze(all_outputs[len(angle_heads)+len(arrow_heads) : len(angle_heads)+len(arrow_heads)+len(arrow_turn_heads)])[:, 1]) > 0.5)
arrow_turn_right = int(np.mean(np.squeeze(all_outputs[len(angle_heads)+len(arrow_heads) : len(angle_heads)+len(arrow_heads)+len(arrow_turn_heads)])[:, 2]) > 0.5)

In [53]:
angle_output = float(np.mean(np.squeeze(all_outputs[0:len(angle_heads)])))

# arrow_left = float(np.squeeze(all_outputs[1]))
# arrow_right = float(np.squeeze(all_outputs[2]))

# arrow_left_turn = float(np.squeeze(all_outputs[3]))
# arrow_right_turn = float(np.squeeze(all_outputs[4]))

# speed_output = int(np.squeeze(all_outputs[-1])[0] > 0.5)

speed_output = int(np.mean(np.squeeze(all_outputs[-5:])[:,0]) > 0.5)

# # Split into angle_outputs (0-9) and speed_outputs (10-19)
# angle_outputs = np.array(all_outputs[:10])
# speed_outputs = np.array(all_outputs[10:])

# angle_outputs.mean(), speed_outputs.mean()
angle_output

0.7329090237617493

In [54]:
print(angle_output, arrow_left, arrow_right, arrow_left_turn, arrow_right_turn, speed_output)

NameError: name 'arrow_left_turn' is not defined